# HAPI‑FHIR + Synthea Sandbox (PowerShell Edition)

This notebook reproduces the entire setup and validation workflow we walked through in chat, but every shell cell is written for **PowerShell** instead of Git Bash.  Run the cells step‑by‑step in VS Code’s Jupyter view (kernel: *Python* is fine because each shell cell is self‑contained).

## Prerequisites
* Docker Desktop running locally
* Synthea export folder at `D:\synthea_out\fhir` (one **transaction Bundle** JSON per patient)
* A PowerShell‑enabled Jupyter environment (VS Code does this automatically when you prefix cells with `%%powershell`)

## 1  Start (or restart) the HAPI‑FHIR server container


**Option A – PostgreSQL persistence**
Use `docker-compose.yml` to run HAPI-FHIR with PostgreSQL (recommended for large imports)
Use Docker Compose with the provided `docker-compose.yml` to launch HAPI‑FHIR backed by PostgreSQL. This avoids the H2 memory limits when loading many bundles. Run the commands below in a PowerShell terminal:


```powershell
docker compose down          # stop and remove old containers
docker compose pull          # fetch images
docker compose up -d         # start stack
docker compose logs -f hapi  # wait for 'Started Application'
```



**Option B – H2 with on-disk files**
Start with `docker-compose-h2.yml` and restart the container as needed to free memory:


In [10]:
# Option B – Restart H2-based HAPI-FHIR container via Python subprocess
import subprocess

commands = [
    ["docker", "compose", "-f", "docker-compose-h2.yml", "down"],      # stop H2 stack
    ["docker", "compose", "-f", "docker-compose-h2.yml", "up", "-d"], # start stack
    ["docker", "compose", "-f", "docker-compose-h2.yml", "logs", "-f", "hapi"],
    ["docker", "compose", "logs", "-f", "hapi"]                        # follow logs until started
]

for cmd in commands:
    print(f"Running: {' '.join(cmd)}")
    result = subprocess.run(cmd, capture_output=True, text=True)
    print(result.stdout)
    if result.stderr:
        print("Error:", result.stderr)

Running: docker compose -f docker-compose-h2.yml down

Error:  Container hapi-fhir  Stopping
 Container hapi-fhir  Stopped
 Container hapi-fhir  Removing
 Container hapi-fhir  Removed
 Network self_learning_healthcarebigdata_default  Removing
 Network self_learning_healthcarebigdata_default  Removed

Running: docker compose -f docker-compose-h2.yml up -d

Error:  Container hapi-fhir  Stopping
 Container hapi-fhir  Stopped
 Container hapi-fhir  Removing
 Container hapi-fhir  Removed
 Network self_learning_healthcarebigdata_default  Removing
 Network self_learning_healthcarebigdata_default  Removed

Running: docker compose -f docker-compose-h2.yml up -d

Error:  Network self_learning_healthcarebigdata_default  Creating
 Network self_learning_healthcarebigdata_default  Created
 Container hapi-fhir  Creating
 Container hapi-fhir  Created
 Container hapi-fhir  Starting
 Container hapi-fhir  Started

Running: docker compose -f docker-compose-h2.yml logs -f hapi

Error:  Network self_learning

## 2  Set local variables

In [11]:
import subprocess

# Define paths and URL
powershell_script = """
$BUNDLE_DIR = '//Desktop-family/K/synthea_out/fhir'  # Updated to match the path in prerequisites
$FHIR_BASE  = "http://localhost:8080/fhir/"
Write-Host "BUNDLE_DIR set to: $BUNDLE_DIR"
Write-Host "FHIR_BASE set to: $FHIR_BASE"

# Set these variables as environment variables so they persist for future cells
[Environment]::SetEnvironmentVariable("BUNDLE_DIR", $BUNDLE_DIR, "Process")
[Environment]::SetEnvironmentVariable("FHIR_BASE", $FHIR_BASE, "Process")
"""

# Execute PowerShell script
result = subprocess.run(["powershell", "-Command", powershell_script], capture_output=True, text=True)
print(result.stdout)
if result.stderr:
    print("Error:", result.stderr)

# Store in Python variables for potential use in Python cells
BUNDLE_DIR = '//Desktop-family/K/synthea_out/fhir'
FHIR_BASE = "http://localhost:8080/fhir/"

BUNDLE_DIR set to: //Desktop-family/K/synthea_out/fhir
FHIR_BASE set to: http://localhost:8080/fhir/



### Health check: CapabilityStatement should return JSON

In [12]:
import subprocess

# PowerShell script to check FHIR server health with explicit URL
ps_script = """
$FHIR_BASE = "http://localhost:8080/fhir/"
Invoke-RestMethod -Uri ($FHIR_BASE + "metadata") | ConvertTo-Json -Depth 1 | Select-Object -First 20
"""

# Execute PowerShell script
result = subprocess.run(["powershell", "-Command", ps_script], capture_output=True, text=True)
print(result.stdout)
if result.stderr:
    print("Error:", result.stderr)


Error: Invoke-RestMethod : The underlying connection was closed: The connection was closed unexpectedly.
At line:3 char:1
+ Invoke-RestMethod -Uri ($FHIR_BASE + "metadata") | ConvertTo-Json -De ...
+ ~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
    + CategoryInfo          : InvalidOperation: (System.Net.HttpWebRequest:HttpWebRequest) [Invoke-RestMethod], WebExc 
   eption
    + FullyQualifiedErrorId : WebCmdletWebResponseException,Microsoft.PowerShell.Commands.InvokeRestMethodCommand
 



## 3  Upload every Synthea transaction bundle

1. Verify Docker container is running properly


In [13]:
import subprocess

ps_script = """
# Check if HAPI FHIR container is running
Write-Output "Checking Docker container status:"
docker ps -a | Select-String -Pattern "hapi"

# Check container logs for errors
Write-Output "`nContainer logs (last 20 lines):"
docker logs --tail 20 hapi
"""

result = subprocess.run(["powershell", "-Command", ps_script], capture_output=True, text=True)
print(result.stdout)
if result.stderr:
    print("Error:", result.stderr)

Checking Docker container status:

0b2412c6e3bc   hapiproject/hapi:v8.2.0-1   "java --class-path /…"   36 seconds ago   Exited (1) 1 second ago         
    hapi-fhir

Container logs (last 20 lines):



Error: Error response from daemon: No such container: hapi



2. Test basic connectivity to the FHIR server


In [14]:
import subprocess

ps_script = """
Write-Output "Testing basic connectivity to FHIR server..."
try {
    $response = Invoke-WebRequest -Uri "http://localhost:8080/fhir/metadata" -TimeoutSec 5
    Write-Output "Connection successful! Status code: $($response.StatusCode)"
} catch {
    Write-Output "Failed to connect: $_"
    
    # Check if service is listening on port
    Write-Output "`nChecking port 8080:"
    netstat -ano | findstr :8080
}
"""

result = subprocess.run(["powershell", "-Command", ps_script], capture_output=True, text=True)
print(result.stdout)
if result.stderr:
    print("Error:", result.stderr)

Testing basic connectivity to FHIR server...
Failed to connect: Unable to connect to the remote server

Checking port 8080:
  TCP    [::1]:8080             [::1]:60215            TIME_WAIT       0
  TCP    [::1]:8080             [::1]:60216            TIME_WAIT       0



3. Wait for server to initialize (this is critical):


In [15]:
import subprocess
import time

print("Waiting for HAPI FHIR server to initialize...")
ps_script = """
$maxAttempts = 12
$attempt = 0
$success = $false

while (-not $success -and $attempt -lt $maxAttempts) {
    $attempt++
    Write-Output "Connection attempt $attempt of $maxAttempts..."
    
    try {
        $response = Invoke-WebRequest -Uri "http://localhost:8080/fhir/metadata" -TimeoutSec 10
        if ($response.StatusCode -eq 200) {
            Write-Output "Server is up and running! Status code: $($response.StatusCode)"
            $success = $true
        }
    } catch {
        Write-Output "Still waiting for server... ($($_.Exception.Message))"
        Start-Sleep -Seconds 10
    }
}

if (-not $success) {
    Write-Output "Server did not become available after $(10*$maxAttempts) seconds"
} else {
    Write-Output "HAPI FHIR server is ready to use"
}
"""

result = subprocess.run(["powershell", "-Command", ps_script], capture_output=True, text=True)
print(result.stdout)

Waiting for HAPI FHIR server to initialize...
Connection attempt 1 of 12...
Still waiting for server... (Unable to connect to the remote server)
Connection attempt 2 of 12...
Still waiting for server... (Unable to connect to the remote server)
Connection attempt 3 of 12...
Still waiting for server... (Unable to connect to the remote server)
Connection attempt 4 of 12...
Still waiting for server... (Unable to connect to the remote server)
Connection attempt 5 of 12...
Still waiting for server... (Unable to connect to the remote server)
Connection attempt 6 of 12...
Still waiting for server... (Unable to connect to the remote server)
Connection attempt 7 of 12...
Still waiting for server... (Unable to connect to the remote server)
Connection attempt 8 of 12...
Still waiting for server... (Unable to connect to the remote server)
Connection attempt 9 of 12...
Still waiting for server... (Unable to connect to the remote server)
Connection attempt 10 of 12...
Still waiting for server... (Una


The script now skips bundles larger than 5 MB to avoid exhausting the H2 database.

5. Testing if a HAPI FHIR Server is Running Correctly


In [ ]:
import subprocess, sys

ps_script = r"""
$fhirBase = "http://localhost:8080/fhir"
$results = [ordered]@{}

Write-Output "========== HAPI FHIR SERVER HEALTH CHECK =========="

# 1. Basic connectivity test
Write-Output "`n1. Testing basic connectivity..."
try {
    $response = Invoke-WebRequest -Uri "$fhirBase/metadata" -TimeoutSec 5 -UseBasicParsing
    $results["Basic Connectivity"] = "OK (Status: $($response.StatusCode))"
    Write-Output "Server is reachable! Status code: $($response.StatusCode)"
} catch {
    $results["Basic Connectivity"] = "FAILED: $($_.Exception.Message)"
    Write-Output "Failed to connect: $($_.Exception.Message)"
}
"""

print("Running comprehensive HAPI FHIR server health check...")
result = subprocess.run(["powershell", "-NoLogo", "-NoProfile", "-Command", ps_script], 
                        capture_output=True, text=True)

print(result.stdout)
if result.stderr:
    print("STDERR:", result.stderr, file=sys.stderr)

In [ ]:

# 2. Check server version and capabilities
import subprocess, sys

ps_script = r"""
$fhirBase = "http://localhost:8080/fhir"
$results = [ordered]@{}

Write-Output "========== HAPI FHIR SERVER HEALTH CHECK =========="
try {
    $metadata = Invoke-RestMethod -Uri "$fhirBase/metadata" -TimeoutSec 10
    $version = $metadata.software.version
    $fhirVersion = $metadata.fhirVersion
    $results["Server Version"] = $version
    $results["FHIR Version"] = $fhirVersion
    
    Write-Output "   Server info: HAPI FHIR $version (FHIR $fhirVersion)"
    
    # List supported resource types
    $resourceTypes = $metadata.rest.resource.type | Sort-Object -Unique
    $results["Resource Types"] = "$($resourceTypes.Count) types supported"
    Write-Output "   Supports $($resourceTypes.Count) resource types"
    
    # Check if common resources are supported
    $commonTypes = @("Patient", "Observation", "Encounter", "Condition")
    foreach ($type in $commonTypes) {
        if ($resourceTypes -contains $type) {
            Write-Output "   Supports $type resources"
        } else {
            Write-Output "Does NOT support $type resources"
        }
    }
    
    # List operations
    $operations = $metadata.rest.operation.name | Sort-Object -Unique
    if ($operations) {
        $results["Operations"] = "$($operations.Count) operations supported"
        Write-Output "   Supports $($operations.Count) operations: $($operations -join ', ')"
    } else {
        $results["Operations"] = "None found"
        Write-Output "No operations found in capabilities statement"
    }
    
} catch {
    $results["Server Capabilities"] = " FAILED: $($_.Exception.Message)"
    Write-Output "   Failed to retrieve capabilities: $($_.Exception.Message)"
}
"""

print("Running comprehensive HAPI FHIR server health check...")
result = subprocess.run(["powershell", "-NoLogo", "-NoProfile", "-Command", ps_script], 
                        capture_output=True, text=True)

print(result.stdout)
if result.stderr:
    print("STDERR:", result.stderr, file=sys.stderr)
    
